In [1]:

import sys
import os
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from qgis.core import *
from qgis.PyQt.QtGui import *
from qgis.PyQt.QtCore import *
from IPython.display import Image

In [2]:
QgsApplication.setPrefixPath(r'C:\\OSGeo4W64\\apps\\qgis', True)
qgs = QgsApplication([], True)
qgs.initQgis()
sys.path.append(r'C:\OSGeo4W64\apps\qgis\python\plugins')
project = QgsProject.instance()

In [3]:
path = "mapa/SWE_adm1.shp"

map_layer = QgsVectorLayer(path, 'SWE_adm1', 'ogr')

if not map_layer.isValid():
    print("Failed to load the layer!")
else:
    project.addMapLayer(map_layer)
    print("Sucess")

Sucess


In [4]:
csv_path = "file:///C:/OSGeo4W64/bin/Epidemiologia1/Sweden/dados/time_series_confimed-confirmed.csv"


csv_layer = QgsVectorLayer(csv_path, 'Data', 'delimitedtext')

if not csv_layer.isValid():
    print('Layer failed to load!')
else:
    project.addMapLayer(csv_layer)
    print("Sucess")

Sucess


In [5]:
joinName = 'Display_Name'
targetName = 'NAME_1'

joinObject = QgsVectorLayerJoinInfo()
joinObject.setJoinFieldName(joinName)
joinObject.setTargetFieldName(targetName)
joinObject.setJoinLayerId(csv_layer.id())
joinObject.setUsingMemoryCache(True)
joinObject.setJoinLayer(csv_layer)
flag = map_layer.addJoin(joinObject)

In [6]:
death_layer = map_layer.clone()
death_layer.setName("Hospital_Total")
for field in death_layer.fields():
    print("Column "+field.name()+" Load")

Column ID_0 Load
Column ISO Load
Column NAME_0 Load
Column ID_1 Load
Column NAME_1 Load
Column TYPE_1 Load
Column ENGTYPE_1 Load
Column NL_NAME_1 Load
Column VARNAME_1 Load
Column Data_Region Load
Column Data_Population Load
Column Data_Lat Load
Column Data_Long Load
Column Data_25/02/2020 Load
Column Data_26/02/2020 Load
Column Data_27/02/2020 Load
Column Data_28/02/2020 Load
Column Data_29/02/2020 Load
Column Data_01/03/2020 Load
Column Data_02/03/2020 Load
Column Data_03/03/2020 Load
Column Data_04/03/2020 Load
Column Data_05/03/2020 Load
Column Data_06/03/2020 Load
Column Data_07/03/2020 Load
Column Data_08/03/2020 Load
Column Data_09/03/2020 Load
Column Data_10/03/2020 Load
Column Data_11/03/2020 Load
Column Data_12/03/2020 Load
Column Data_13/03/2020 Load
Column Data_14/03/2020 Load
Column Data_15/03/2020 Load
Column Data_16/03/2020 Load
Column Data_17/03/2020 Load
Column Data_18/03/2020 Load
Column Data_19/03/2020 Load
Column Data_20/03/2020 Load
Column Data_21/03/2020 Load
Colu

In [7]:
from qgis.utils import iface


label_settings = QgsPalLayerSettings()
label_settings.drawBackground = True
label_settings.fieldName = "NAME_1"

text_format = QgsTextFormat()

text_format.setFont(QFont("Arial", 12))
text_format.setSize(55) 
                     
background_color = QgsTextBackgroundSettings()
text_format.setColor(QColor("black"))

background_color.setEnabled(False)
text_format.setBackground(background_color )
label_settings.setFormat(text_format)

death_layer.setLabeling(QgsVectorLayerSimpleLabeling(label_settings))
death_layer.setLabelsEnabled(True)
death_layer.triggerRepaint()

In [8]:
from qgis.PyQt import QtGui

myOpacity = 1

myTargetField = "Data_Hospital_Total"
myRangeList = []

myMin = 0
myMax = 15
myLabel = '0-15'
myColour = QtGui.QColor('#f7fbff')
mySymbol = QgsSymbol.defaultSymbol(death_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 16
myMax = 50
myLabel = '16-50'
myColour = QtGui.QColor('#b0d2e8')
mySymbol = QgsSymbol.defaultSymbol(death_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 50
myMax = 392
myLabel = '50-250'
myColour = QtGui.QColor('#3e8ec4')
mySymbol = QgsSymbol.defaultSymbol(death_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)


myMin = 250
myMax = 1000
myLabel = '250 - 1000'
myColour = QtGui.QColor('#08306b')
mySymbol = QgsSymbol.defaultSymbol(death_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)





myMin = -1
myMax = -1
myLabel = 'Sem Dados'
myColour = QtGui.QColor('#333333')
mySymbol = QgsSymbol.defaultSymbol(death_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)
myRenderer = QgsGraduatedSymbolRenderer('', myRangeList)
myClassificationMethod = QgsApplication.classificationMethodRegistry().method("EqualInterval")
myRenderer.setClassificationMethod(myClassificationMethod)
myRenderer.setClassAttribute(myTargetField)

death_layer.setRenderer(myRenderer)

In [9]:
xt = death_layer.extent()
width  = 1024
height = int(width*xt.height()/xt.width())

manager = project.layoutManager()
layout = QgsPrintLayout(project)
layout.initializeDefaults()
manager.addLayout(layout)

pc = layout.pageCollection()
pc.page(0).attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

map = QgsLayoutItemMap(layout)
map.setRect(1,1,1,1)
map.setLayers([death_layer])

options = QgsMapSettings()
options.setLayers([death_layer])
options.setOutputSize(QSize(width, height))
options.setExtent(xt)
map.setExtent(xt)
map.setBackgroundColor(QColor(255, 255, 255))

layout.addLayoutItem(map)

map.attemptMove(QgsLayoutPoint(0,0,QgsUnitTypes.LayoutMillimeters))
map.attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

legend = QgsLayoutItemLegend(layout)
legend.setTitle("Legenda:")
layerTree = QgsLayerTree()
layerTree.addLayer(death_layer)
legend.model().setRootGroup(layerTree)

legend.setRect(1,1,1,1)
legend.setScale(3)
legend.setReferencePoint(6)
legend.attemptMove(QgsLayoutPoint(0,100,QgsUnitTypes.LayoutMillimeters))
legend.setLinkedMap(map)
layout.addLayoutItem(legend)
legend.setLegendFilterByMapEnabled(True)
legend.refresh()

exporter = QgsLayoutExporter(layout)
image = exporter.renderPageToImage(0)

imgbuf= QBuffer()
imgbuf.open(QIODevice.ReadWrite)
image.save(imgbuf,"PNG")
Image(imgbuf.data())